# Computing Koselleck dashboard

In [1]:
from ipynb.fs.full.koselleck import *

[Koselleck] (12:53:07) Alles bereit (+0.0s)


In [2]:
# list of top words
dfanno=read_sheet()#.drop('')
all_words_by_nov = list(get_all_novelty_scores().groupby('word').mean().reset_index().sort_values('foote_novelty_z',ascending=False).drop_duplicates('word').word)
# dfanno

In [3]:
signif_words=set(get_signif_novelty_words(p_peak=0.05))
keywords=get_keywords()
abswords=get_words_ever_abs()

In [4]:
# interact_word=interact.options(manual=True, manual_name="Show data for word")

def show(word='slavery',num_proc=2):
    print('Plotting neighbors',timer=True)
    fig_nbrs=plot_nbrs(word,width=8,height=5,ybin=20,year_min=1720,year_max=1900,max_rank1=10,max_rank=10,min_periods=1)
    print('Plotting distance matrix')
    fig_distmat=plot_historical_semantic_distance_matrix(word)
    print('Plotting novelty scores')
    fig_nov=plot_novelty_words(word,xlim0=1720,xlim1=1900)
    print('Saving temporary files')
    with tempfile.TemporaryDirectory() as tmpdirname:
        fig1fnfn=os.path.join(tmpdirname,'fig1.png')
        fig2fnfn=os.path.join(tmpdirname,'fig2.png')
        fig3fnfn=os.path.join(tmpdirname,'fig3.png')
        fig_nbrs.save(fig1fnfn)
        fig_distmat.save(fig2fnfn)
        fig_nov.save(fig3fnfn)
        
#         print('Creating layout')
        with open(fig1fnfn,'rb') as fig1b, open(fig2fnfn,'rb') as fig2b, open(fig3fnfn,'rb') as fig3b:
            img1=widgets.Image(value=fig1b.read(),format='png')
            img2=widgets.Image(value=fig2b.read(),format='png')
            img3=widgets.Image(value=fig3b.read(),format='png')
#             vb=VBox([img1,img3,img2])
            vl=[img1,img3,img2]
            print('Returning')
            return vl

In [5]:
# show()

In [6]:
# define widgets
widg_word=widgets.Text(value='culture',layout=Layout(width='auto'))
word=widg_word.value
widg_word_submit = widgets.Button(description='Analyze',layout=Layout(width='125px'))
output = widgets.Output()
output2 = widgets.Output()
WD={}

widg_changes = widgets.Text(value='',description='Changes')
widg_from = widgets.Text(value='',description='From')
widg_to = widgets.Text(value='',description='To')
widg_notes = widgets.Text(value='',description='Notes')
widg_valid = widgets.Text(value='',description='is_valid')
savebutton = Button(description='Save annotations')

def do_save(b):
    global dfanno
    print('Reloading metadata before writing',timer=False)
    dfanno1=dfanno=read_sheet()
    
    with output:
#         dfanno1=read_sheet()
        w=widg_word.value
        dfanno1.loc[w,'Changes']=widg_changes.value
        dfanno1.loc[w,'From']=widg_from.value
        dfanno1.loc[w,'To']=widg_to.value
        dfanno1.loc[w,'Notes']=widg_notes.value
        dfanno1.loc[w,'is_valid']=widg_valid.value
#         display(dfanno1.loc[w])
#         display(dfanno1)
        print('Saving online')
        write_sheet(dfanno1)
        print('Finished')
    
def do_anno_save(w,key,value):
    dfanno.loc[w,key]=value
    with output:
        print(f'Saved: {dfanno.loc[w,key]}')
    
def make_edit_widgets(word):
    global WD
    wd={}
    for k,v in dfanno.loc[word].items():
        if k[0]==k[0].upper() or k=='is_valid':
            wd[k]=widgets.Text(description=k, value=v)
    
    wboxes=VBox(list(wd.values()) + [savebutton])
    WD=wd
    return WD,wboxes


# @output.capture(clear_output=True)
def submit_word(w):
    with output:
        widg_word.value=w
        output.clear_output()
        printm(f'## {w}')
        try:
            widg_changes.value=dfanno.loc[w,'Changes']
            widg_from.value=dfanno.loc[w,'From']
            widg_to.value=dfanno.loc[w,'To']
            widg_notes.value=dfanno.loc[w,'Notes']
            widg_valid.value=dfanno.loc[w,'is_valid']
        except KeyError:
            widg_changes.value=''
            widg_from.value=''
            widg_to.value=''
            widg_notes.value=''
            widg_valid.value=''

        wboxes=VBox([widg_changes,widg_from,widg_to,widg_notes,widg_valid,savebutton])
#         display(wboxes,output)
        dfpsgs=show_sents_word(w,num_proc=2,ybin=50,n=5)
        mpsgs=dfpsgs.to_markdown()
        img_nbr,img_nov,img_dist=show(w)
    #         display(show(w),output)
    #         display(info_word_comparisons(w),output2)
    #         display(Markdown(mpsgs),output2)

        i=3
        i2=3
        layout = VBox([
            HBox([
                VBox([
                    markdwn('## '+w),
                    HBox([widg_word,widg_word_submit]),
                    markdwn('### Top 10 closest words over time'),
                    img_nbr,
                    markdwn('### Historical semantic distance matrix'),
                    img_dist,
                    markdwn('### Foote Novelty plot'),
                    img_nov
                ],layout=Layout(width='50%')),
                VBox([
                    markdwn('### Annotations'),
                    wboxes,
                    markdwn('### Top vectors of change'),
                    markdwn(info_word_comparisons(w)),
                    markdwn('### Passages'),
                    markdwn(mpsgs)
                ],layout=Layout(width='50%'))
            ]),
            HBox([
                VBox(
                    [markdwn(f'### Top {lim} Most changing words (p<0.05)')] + \
                    [HBox(buttons[n:n+i]) for n in range(0,len(buttons)+i+1,i)],
                    layout=Layout(border='1px dotted gray')
                ),
                VBox(
                    [markdwn(f'### Top {lim} most changing keywords')] + \
                    [HBox(buttons_kw[n:n+i2]) for n in range(0,len(buttons_kw)+i2+1,i2)],
                    layout=Layout(border='1px dotted gray')
                ),
                VBox(
                    [markdwn(f'### Top {lim} most changing abstractions')] + \
                    [HBox(buttons_abs[n:n+i2]) for n in range(0,len(buttons_abs)+i2+1,i2)],
                    layout=Layout(border='1px dotted gray')
                )
            ])
        ])
        display(layout)
        

# define behaviors
def on_widg_word_submit(b): submit_word(b.value)
def on_widg_word_button_submit(b): submit_word(widg_word.value)
def on_widg_word_button_submit_desc(b): submit_word(b.description.split()[-1])
# set behaviors
widg_word.on_submit(on_widg_word_submit)
widg_word_submit.on_click(on_widg_word_button_submit)
savebutton.on_click(do_save)

def is_anno(w):
    try:
        row=dfanno.loc[w]
    except KeyError:
        return False
    anno=False
    for k,v in row.items():
        if k[0] == k[0].upper() or k=='is_valid':
            if v.strip():
                anno=True
                break
    return anno

# set layout
hb=HBox([widg_word,widg_word_submit])
buttons=[
    widgets.Button(
        description=f'{i+1}. {w}',
        layout=Layout(width='125px', height='25px'),
        style=ButtonStyle(button_color='lightblue' if is_anno(w) else None)
#     ) for i,w in enumerate(dfanno.index[:200])
    ) for i,w in enumerate(get_signif_novelty_words(p_peak=0.01))
]

def make_button(i,w):
    return widgets.Button(
        description=f'{i+1}. {w}',
        layout=Layout(width='125px', height='25px'),
        style=ButtonStyle(button_color='lightblue' if is_anno(w) else None)
#     ) for i,w in enumerate(dfanno.index[:200])
    )
def make_buttons(l):
    return [make_button(i,w) for i,w in l]



lim=200


buttons=make_buttons([(i,w) for i,w in enumerate(all_words_by_nov) if w in signif_words][:lim])
# buttons=make_buttons([(i,w) for i,w in enumerate(all_words_by_nov)][:lim])
buttons_kw=make_buttons([(i,w) for i,w in enumerate(all_words_by_nov) if w in keywords][:lim])
buttons_abs=make_buttons([(i,w) for i,w in enumerate(all_words_by_nov) if w in abswords][:lim])

for b in buttons + buttons_kw + buttons_abs:
    b.on_click(on_widg_word_button_submit_desc)

In [7]:
output

Output()

In [8]:
submit_word('culture')